# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [15 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 399, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 399 (delta 0), reused 2 (delta 0), pack-reused 393
Receiving objects: 100% (399/399), 151.25 MiB | 19.81 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7feaf16fa9d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 15
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 15, 'EVs_n_max': 783, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energ

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13700.34 , over-consume=kWh  32534.67 , under-consume=kWh  18834.33 , Total_cost=€  611.01 , overcost=€  1146.9 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14367.13 , over-consume=kWh  32664.78 , under-consume=kWh  18297.65 , Total_cost=€  608.68 , overcost=€  1134.54 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -5266.34 , over-consume=KWh  2975.59 , under-consume=KWh  8241.93 , Total_cost=€  -109.08 , Overcost=€  104.03 
 EV_INFO: Av.EV_energy_leaving=kWh  70.37 , Std.EV_energy_leaving=kWh  23.65 , EV_departures =  783 , EV_queue_left =  0
SCORE:  Cumulative_reward= 338428.76 - Step_rewars (load_t= 309308.01, EVs_energy_t= 19749.97)
 - Final_rewards (EVs_energy= 14390.34, Overconsume= -2901.83, Underconsume= -4695.68, Overcost= 2577.94)
Episode:1 Score:338428.7612269249


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  61.158581   0.000000   0.000000  52.428722   
2022-01-01 00:15:00  61.408581   0.000000   0.000000  51.240887   
2022-01-01 00:30:00  61.658581   0.000000   0.000000  50.554451   
2022-01-01 00:45:00  61.908581   0.000000   0.000000  49.902130   
2022-01-01 01:00:00  62.158581   0.000000   0.000000  49.124844   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  97.709839  53.556557  52.827450  89.233727   
2022-06-06 05:00:00  98.839432  53.306557  53.957039  90.363319   
2022-06-06 05:15:00  99.612999  54.080124  54.730606  91.136887   
2022-06-06 05:30:00  99.989998  54.813461  55.463943  91.870224   
2022-06-06 05:45:00  99.989998  55.537991  56.188473  92.594757   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 2]   
2022-01-01 00:15:00        [2348, 0, 0, 2349]  [1, 2, 2, 2]   
2022-01-01 00:30:00        [2348, 0, 0, 2349]  [1, 2, 2, 2]   
2022-01-01 00:45:00        [2348, 0, 0, 2349]  [1, 2, 2, 2]   
2022-01-01 01:00:00        [2348, 0, 0, 2349]  [1, 2, 2, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [2683, 2682, 2685, 2684]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [2683, 2682, 2685, 2684]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [2683, 2682, 2685, 2684]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [2683, 2682, 2685, 2684]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [2683, 2682, 2685, 2684]  [1, 1, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00   [False, False, False, True]        1.000000   
2022-01-01 00:30:00   [False, False, False, True]        1.000000   
2022-01-01 00:45:00   [False, False, False, True]        1.000000   
2022-01-01 01:00:00   [True, False, False, False]        1.000000   
...                                           ...             ...   
2022-06-06 04:45:00    [False, False, True, True]        9.772053   
2022-06-06 05:00:00     [False, True, True, True]       13.555088   
2022-06-06 05:15:00    [False, True, True, False]       12.377092   
2022-06-06 05:30:00    [False, True, True, False]       10.308032   
2022-06-06 05:45:00    [False, True, True, False]        8.694366   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.614149e+00    15.000000        0.0   
2022-01-01 00:15:00          -4.751336  0.000000e+00    15.000000        0.0   
2022-01-01 00:30:00          -2.745741  0.000000e+00    15.000000        0.0   
2022-01-01 00:45:00          -2.609283 -2.220446e-16    15.000000        0.0   
2022-01-01 01:00:00          -3.109148  0.000000e+00    15.000000        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000  0.000000e+00    15.000000        0.0   
2022-06-06 05:00:00          -1.000000  1.776357e-15    15.000000        0.0   
2022-06-06 05:15:00           0.000000  0.000000e+00    -0.708897        0.0   
2022-06-06 05:30:00           0.000000 -1.425338e+00    -3.163518        0.0   
2022-06-06 05:45:00           0.000000 -2.898111e+00    -3.716833        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  -0.708897  
2022-06-06 05:30:00  -3.163518  
20

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 3133, Arrival time: 2022-01-01 07:45:00, Parking_time: 24, Leaving_time: 2022-01-02 07:45:00, SOC: 0.6097991783993014, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 3915, Arrival time: 2022-12-31 12:00:00, Parking_time: 23.06286838829129, Leaving_time: 2023-01-01 11:03:46.326198, SOC: 0.5484493986732827, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  5059.82 , over-consume=kWh  27865.6 , under-consume=kWh  22805.79 , Total_cost=€  296.3 , overcost=€  1220.4 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  91.15


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  5065.68 , over-consume=kWh  28430.95 , under-consume=kWh  23365.27 , Total_cost=€  301.8 , overcost=€  1250.65 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  91.15
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -10448.49 , over-consume=KWh  1581.33 , under-consume=KWh  12029.82 , Total_cost=€  -398.28 , Overcost=€  67.59 
 EV_INFO: Av.EV_energy_leaving=kWh  75.06 , Std.EV_energy_leaving=kWh  22.3 , EV_departures =  780 , EV_queue_left =  0
SCORE:  Cumulative_reward= 325998.26 - Step_rewars (load_t= 277873.35, EVs_energy_t= 31396.48)
 - Final_rewards (EVs_energy= 14354.15, Overconsume= -1453.88, Underconsume= -5903.6, Overcost= 9731.77)
Episode:1 Score:325998.26281927864


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  71.263329  43.588367  66.635620  94.372864   
2022-06-06 05:00:00  72.585670  43.338367  67.957962  95.695206   
2022-06-06 05:15:00  73.835304  43.088367  69.207596  96.944839   
2022-06-06 05:30:00  75.045502  42.838367  70.417793  98.155037   
2022-06-06 05:45:00  76.286591  42.588367  71.658882  99.396126   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [5047, 5045, 5046, 5044]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [5047, 5045, 5046, 5044]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [5047, 5045, 5046, 5044]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [5047, 5045, 5046, 5044]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [5047, 5045, 5046, 5044]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00   [True, False, True, False]       11.726628   
2022-06-06 05:00:00   [True, False, True, False]       15.868094   
2022-06-06 05:15:00   [True, False, True, False]       14.995560   
2022-06-06 05:30:00   [True, False, True, False]       14.522350   
2022-06-06 05:45:00   [True, False, True, False]       14.893068   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.478032e+00    -5.009122        0.0   
2022-01-01 00:15:00                0.0 -4.010034e+00    -3.150780        0.0   
2022-01-01 00:30:00                0.0 -2.890468e+00    -3.484669        0.0   
2022-01-01 00:45:00                0.0 -3.090802e+00    -5.316675        0.0   
2022-01-01 01:00:00                0.0 -4.348343e+00    -5.144780        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:00:00               -1.0  1.776357e-15    15.000000        0.0   
2022-06-06 05:15:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:30:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:45:00               -1.0  0.000000e+00    -3.648716       50.1   

                       rewards  
time                            
2022-01-01 00:00:00  -5.009122  
2022-01-01 00:15:00  -3.150780  
2022-01-01 00:30:00  -3.484669  
2022-01-01 00:45:00  -5.316675  
2022-01-01 01:00:00  -5.144780  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:4

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5482, Arrival time: 2022-01-01 15:45:00, Parking_time: 24, Leaving_time: 2022-01-02 15:45:00, SOC: 0.455959874178415, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6264, Arrival time: 2022-12-31 17:45:00, Parking_time: 24, Leaving_time: 2023-01-01 17:45:00, SOC: 0.4459749077013221, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  2104.83 , over-consume=kWh  27050.15 , under-consume=kWh  24945.32 , Total_cost=€  211.34 , overcost=€  1118.61 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  95.56


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  1461.23 , over-consume=kWh  26695.44 , under-consume=kWh  25234.2 , Total_cost=€  216.42 , overcost=€  1127.07 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  95.56
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -12022.11 , over-consume=KWh  1338.63 , under-consume=KWh  13360.74 , Total_cost=€  -410.64 , Overcost=€  57.17 
 EV_INFO: Av.EV_energy_leaving=kWh  78.38 , Std.EV_energy_leaving=kWh  21.19 , EV_departures =  781 , EV_queue_left =  0
SCORE:  Cumulative_reward= 336105.04 - Step_rewars (load_t= 279202.76, EVs_energy_t= 39028.29)
 - Final_rewards (EVs_energy= 14919.56, Overconsume= -1230.39, Underconsume= -6177.55, Overcost= 10362.38)
Episode:1 Score:336105.0436357194


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0          1          2    3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:15:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:30:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:45:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 01:00:00   0.000000   0.000000   0.000000  0.0   
...                        ...        ...        ...  ...   
2022-06-06 03:30:00  99.489998  87.403915  44.481220  0.0   
2022-06-06 03:45:00  99.239998  88.110687  45.187988  0.0   
2022-06-06 04:00:00  98.989998  89.119095  46.196400  0.0   
2022-06-06 04:15:00  99.548859  89.677956  46.755260  0.0   
2022-06-06 04:30:00  99.989998  89.677956  47.722630  0.0   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                    ...           ...   
2022-06-06 03:30:00  [7390, 7389, 7391, 0]  [2, 1, 1, 2]   
2022-06-06 03:45:00  [7390, 7389, 7391, 0]  [2, 1, 1, 2]   
2022-06-06 04:00:00  [7390, 7389, 7391, 0]  [1, 1, 1, 2]   
2022-06-06 04:15:00  [7390, 7389, 7391, 0]  [1, 0, 1, 2]   
2022-06-06 04:30:00  [7390, 7389, 7391, 0]  [1, 1, 1, 2]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [False, True, True, False]        6.297092   
2022-06-06 03:45:00   [False, True, True, False]        5.654150   
2022-06-06 04:00:00   [False, True, True, False]        8.067286   
2022-06-06 04:15:00   [False, True, True, False]        6.706351   
2022-06-06 04:30:00   [False, True, True, False]        5.634045   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -2.924424e+00    -4.346444        0.0   
2022-01-01 00:15:00                0.0 -3.607866e+00    -4.547658        0.0   
2022-01-01 00:30:00                0.0 -3.728595e+00    -4.267027        0.0   
2022-01-01 00:45:00                0.0 -3.560216e+00    -6.426711        0.0   
2022-01-01 01:00:00                0.0 -5.569382e+00    -6.564346        0.0   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -2.0  0.000000e+00    15.000000        0.0   
2022-06-06 03:45:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:00:00               -1.0  8.881784e-16    15.000000        0.0   
2022-06-06 04:15:00                0.0 -8.881784e-16    -1.841524        0.0   
2022-06-06 04:30:00                0.0 -2.104914e+00    -2.450955        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.346444  
2022-01-01 00:15:00  -4.547658  
2022-01-01 00:30:00  -4.267027  
2022-01-01 00:45:00  -6.426711  
2022-01-01 01:00:00  -6.564346  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.000000  
2022-06-06 04:15:00  -1.841524  
2022-06-06 04:30:00  -2.450955  

[14995 rows x 13 columns]

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [63]:
#env.close()